# Entrainement inspiré par mosaicml/mpt-7b-instruct

## Installation des librairies manquantes

In [ ]:
! pip install bitsandbytes
! pip install einops
! pip install peft
! pip install trl

# Bug selon la version de datasets, besoin d'installer une version plus récente que celle de l'environnement pré-installé :
! pip uninstall datasets -y
! pip install datasets==2.13.1

import datasets
datasets.__version__

## Import des librairies

In [ ]:
import einops
import torch
from datasets import load_dataset
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig, TrainingArguments
from peft import LoraConfig
from trl import SFTTrainer

## Téléchargement du dataset pour le fine tuning

In [ ]:

dataset_name = "Laurent1/MedQuad-MedicalQnADataset_128tokens_max"
# On fine tune les 5000 premieres questions sinon c'est un peu long...
dataset = load_dataset(dataset_name, split='train[:5120]')
dataset


## Téléchargement du model pre-entrainé et de son tokenizer

In [ ]:
model_name = "ibm/mpt-7b-instruct2"

# BitsAndBytes permet le fine tuning avec "quantification" pour réduire l'impact mémoire et les calculs
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.float16,
)

model = AutoModelForCausalLM.from_pretrained(
        "ibm/mpt-7b-instruct2",
        device_map="auto",
        torch_dtype=torch.float16, #torch.bfloat16,
        trust_remote_code=True
            )

tokenizer = AutoTokenizer.from_pretrained(model_name)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"

## Configuration du peft LoRa

In [ ]:
lora_alpha = 16
lora_dropout = 0.1
lora_r = 32

peft_config = LoraConfig(
    lora_alpha=lora_alpha,
    lora_dropout=lora_dropout,
    r=lora_r,
    bias="none",
    task_type="CAUSAL_LM",
    target_modules=[
        "Wqkv",
        "out_proj",
        "up_proj",
        "down_proj",
    ]
)

## Préparation de l'entraineur (Supervised Fine-tuning Trainer)

Utilisation de [`SFTTrainer` de la librairie TRL](https://huggingface.co/docs/trl/main/en/sft_trainer) qui est un wrapper de Trainer facilite le fine tuning avec LoRa

In [ ]:
output_dir = "/YOUR DIRECTORY"
per_device_train_batch_size = 1
gradient_accumulation_steps = 16
optim = "paged_adamw_32bit"
save_steps = 64
logging_steps = 64
learning_rate = 1e-4
max_grad_norm = 0.3
max_steps = 1600
warmup_ratio = 0.03
lr_scheduler_type = "linear"

training_arguments = TrainingArguments(
    output_dir=output_dir,
    per_device_train_batch_size=per_device_train_batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    optim=optim,
    save_steps=save_steps,
    logging_steps=logging_steps,
    learning_rate=learning_rate,
    fp16=True,
    max_grad_norm=max_grad_norm,
    max_steps=max_steps,
    warmup_ratio=warmup_ratio,
    group_by_length=True,
    lr_scheduler_type=lr_scheduler_type,
    report_to = 'none',
    save_total_limit = 1
)

In [ ]:
trainer = SFTTrainer(
    model=model,
    train_dataset=dataset,
    peft_config=peft_config,
    dataset_text_field="text",
    max_seq_length= 512,
    tokenizer=tokenizer,
    args=training_arguments,
)

## Entrainement du model

In [ ]:
trainer.train()

You're using a GPTNeoXTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.


TrainOutput(global_step=1600, training_loss=0.819993417263031, metrics={'train_runtime': 6042.1301, 'train_samples_per_second': 4.237, 'train_steps_per_second': 0.265, 'total_flos': 1.0172436457734144e+17, 'train_loss': 0.819993417263031, 'epoch': 5.0})

In [ ]:

text = "Below is an instruction from Human. Write a response.\n    ### Instruction:\n   How to diagnose Parasites - Baylisascaris infection ?\n    ### Response:"
inputs = tokenizer(text, return_tensors="pt").to('cuda')
out = model.generate(**inputs, max_new_tokens=100)

print(tokenizer.decode(out[0]))


/opt/conda/lib/python3.10/site-packages/transformers/generation/utils.py:1417: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation )
  warnings.warn(


Below is an instruction from Human. Write a response.
    ### Instruction:
   How to diagnose Parasites - Baylisascaris infection?
    ### Response:
    The infection is diagnosed by identification of the parasite in stool samples.
    
The infection is usually diagnosed after the person has been hospitalized and the diagnosis is confirmed by identification of the parasite in stool samples.
    
The stool samples are sent to a laboratory for examination.
    ### Instruction:
    How to prevent and control Parasites - Baylisascaris infection?
    ### Response:
    The best way to prevent infection is to avoid contact with raccoons
